## ELEX 4653 Lab 3

This lab provides practice on strings, and regular expressions.

_Version 2: clarified wording of Questions 3 and 4; added extra test case to Question 4._

Instructions:

- Modify this notebook by adding the Python code described below.

- Test your code using the menu item `Cell  ► Run All` or `Run ► Run All Cells`

- Save the notebook (the .ipynb file) and upload it to the appropriate Assignment folder on the course web site.

#### Question 1

Define a function `rearrange(s)` that returns a string composed of the words in the string `s` arranged in alphabetical order.  Words in `s` are separated by a single space.

For example, `rearrange("the quick brown fox jumps over the lazy dog")` should return `'brown dog fox jumps lazy over quick the the'`.

#### Question 2

Define a function `vowelfreq(s)` that returns a list of two-element tuples whose first element is a vowel and the second element is the number of times that vowel appears in the string `s`.  For this question vowels include the letters `a`, `e`, `i`, `o`, and `u` (both upper and lower case).

For example, `vowelfreq("The quick BROWN fox")` returns `[('a', 0), ('e', 1), ('i', 1), ('o', 2), ('u', 1)]`.

#### Question 3

Declare a function named `closest(p,l)` where `p` is an `(x,y,z)` 3D coordinate tuple and `l` is a list of these.  The function  should return a 3D coordinate tuple of the point in `l` closest (smallest Euclidian distance) to `p`.

For example, `closest((1,1,1),[(0,0,0), (1,0,1), (1,0.1,1), (2,2,2)])` returns `(1, 0.1, 1)`.

#### Question 4

Write a function `validate(l)` that is passed a list of strings `l` and returns a list of the strings that exactly match the following pattern:

* one upper-case letter, not including the letter L ("El"), followed by
* one optional upper-case letter, followed by
* one or two digits, followed by
* one optional upper-case letter, followed by
* a space, followed by
* a digit, followed by
* two upper-case letters.

For example:
```
l = ['SW1A 1AA',  'W1A 1AA',   'OX1 2JD', 'CB2 1TN', 'NW10 6XE',
     'ABC1A 1AA', 'CB225 1TN', 'OX12JD',  'W1A AA',  'SW1A 1AAA',
     'SW1A 1AA ', ' SW1A 1AA']

validate(l) 
```

would return: `['SW1A 1AA', 'W1A 1AA', 'OX1 2JD', 'CB2 1TN', 'NW10 6XE']`

_Hint: use a regular expression._


### Question 5

Some IC part numbers are composed of a prefix of one or two upper-case letters, a number, and a suffix composed of upper-case letters.  

Write a function named `fixpartnums(l)` that returns a list of the part numbers in the list `l` modified so that the suffix comes first, followed by a hyphen (-), followed by the prefix and the number.

For example, `fixpartnums(['V243PC', 'DC997VPU', 'L384IVX', 'V926OZ', 'Y404GK'])` would return `['PC-V243', 'VPU-DC997', 'IVX-L384', 'OZ-V926', 'GK-Y404']`.

_Hint: Use `re.sub()`._


In [9]:
# lab validation code; do not modify
def labcheck(testing=0,ntest=10):
    '''
    Python exercise checking.
    Ed.Casas 2023-5-22
    Calls functions q<n>* and checks HMAC of return value[0].
    On mismatch prints return value[1] (function, arguments and return values).
    Setting testing=1 prints HMACs of correct results; paste into 'hashvalues'.
    Note:
    If q<n>* result not JSON-able, convert to string.
    Result order matters for comparison. Sort result if ordering not important.
    '''
    
    import base64, copy, hashlib, json, random, re, string, types 
    from random import randint
    import traceback
    
    # compare regex to strings that should/shouldn't match
    def checkre(pat,ok,nok):
        for s in ok:
            assert re.search(pat,s), \
                f"pattern '{pat}'\n did not match string '{s}'"
        for s in nok:
            assert not re.search(pat,s), \
                f"pattern '{pat}'\n matched string '{s}'"  
    
    # list of n words with nl letters from chars without repeats
    def randwords(n,chars=string.ascii_lowercase,nl=(2,5)):
        l = []
        while len(l)<n:
            w = ''.join([chars[randint(0,len(chars)-1)] for i in range(randint(*nl))])
            if w not in l:
                l.append(w)
        return l
    
    # convert sets to dicts and dict keys to strings so they can be sorted
    def orderkeys(o):
        if isinstance(o,set):
            return {str(k):None for k in o}
        if isinstance(o,dict):
            return {str(k):orderkeys(v) for k,v in o.items()}
        return o
    
    import math
    def roundn(num, n):
        return 0 if not num else round(num, -int(math.floor(math.log10(abs(num)))) + (n - 1))

    def ch(s,n=(1,1)):
        return randwords(1,chars=s,nl=n)[0]

    import ast, inspect
    def uses(f,s):
        for t in ast.walk(ast.parse(inspect.getsource(f))):
            if isinstance(t, ast.Call):
                if isinstance(t.func, ast.Name) and t.func.id == s:
                    return True
        return False
    
    class notalist(list):
        def __getitem__(self, index):
            raise TypeError("Indexing is not allowed, use the iterator.")

    def Q(f,a,*,rounding=None):
        oa = copy.deepcopy(a)
        r = f(*a)
        r = roundn(r,rounding) if rounding else r
        return (r,f"{f.__name__}{repr(oa)} returns {repr(r)}")

    def Q1():
        return Q(rearrange,(' '.join(randwords(randint(5,8))),))
    
    def Q2():
        return Q(vowelfreq,(randwords(1,chars="ABXDEfghijIOUou",nl=(10,20))[0],))
    
    def Q3():
        def triple():
            return tuple([randint(0,9) for i in range(3)])
        return Q(closest,(triple(),[triple() for i in range(randint(3,5))]))
    
    def Q4():
        l = ['SW1A 1AA', 'W1A 1AA',  'OX1 2JD', 'CB2 1TN', 'NW10 6XE',
             'ABC1A 1AA', 'CB225 1TN','OX12JD',  'W1A AA',  'SW1A 1AAA', 'LW1A 1AA', 
             'SW1A 1AA ', ' SW1A 1AA']
        random.shuffle(l)
        for j, s in enumerate(l):
            s = list(s)
            for i,c in enumerate(s):
                if c == 'L':
                    s[i]='L'
                elif i == 0 and c.isupper():
                    s[i]=random.choice('ABCDEFGHIJKMNOPQRSTUVWXYZ')
                elif c.isupper():
                    s[i]=random.choice(string.ascii_uppercase)
                elif c.isdigit():
                    s[i]=random.choice(string.digits)
                else:
                    s[i]=c
            l[j] = ''.join(s)    
        return Q(validate,(l,))
    
    def Q5():
        l = []
        for i in range(randint(5,8)):
            p1 = ''.join([random.choice(string.ascii_uppercase) for i in range(randint(1,2))])
            p2 = str(randint(10,1000))
            p3 = ''.join([random.choice(string.ascii_uppercase) for i in range(randint(1,3))])
            l.append(p1+p2+p3)
        return Q(fixpartnums,(l,))

    hashvalues = '''
rLy8mnTEMkaaPcq6JY3oSt7OgDbd2TLbpixzRwhL
kLyxWfcZTVQJWHqHTm7K54iq/20XlIe0Qj8oQ7cQ
ZA/qUh4BI35Dq962l3rZUig9GayY/yYGyCq6XdtG
zS3BENogdL6FbtbMJJDOw2yNbcOiKSXmVZskL2nP
pscvF59zrqmk3C46bdRLEP9kjnOHye2CZiSE8nUo
'''.split()

    newhash = ''
    dsize = 3 # HMAC base64 digest size (bytes, use 3 or 6 for 4 or 8 char digests)
    dlen = ((dsize*8+5)//6+3)//4*4
           
    for n,f in [(n,f) for n,f in locals().items() if callable(f) and re.search(r'^[Qq]\d+.*',n)]:
        random.seed(n)      
        hashes = '0'*dlen*ntest if testing else hashvalues.pop(0)
        err = ''
        while hashes and not err:
            h, hashes = hashes[:dlen], hashes[dlen:] 
            try:
                v,s = f()
                b = json.dumps(orderkeys(v),sort_keys=True).encode()
                c = base64.b64encode(hashlib.blake2b(b,digest_size=dsize).digest()).decode()
                if testing:
                    print(s)
                    newhash += c
                else:
                    if c != h:
                        err = f"Wrong result for test {n}: {s} (HMAC={c} instead of {h})"
            except Exception as e:
                traceback.print_exc()
                err = f"Error during test {n}: {e}"               
        if testing:
           newhash += '\n'
        else:
            print(err or f"Passed test {n}.")
            
    if testing:
        print(newhash)

labcheck(0)